In [2]:
from __future__ import print_function

import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
%matplotlib inline

import math as m
from time import time
from scipy import stats
from scipy import optimize
import scipy as sp

In [3]:
import sys
print (sys.version)
if sys.version_info >= (3,4):
    print( "with enums" )
    from enum import Enum
    class CallPut(Enum):
        call = 1
        put = 2
else:
    print( "no enums" )
    class CallPut(object):
        __values__ = ['call', 'put']
        
        def __init__(self, t, s):
            self.value = t
            self.str_value = s

        
        def __eq__(self,y):
            if type(y) is not self.__class__:
                return False
            return self.value == y.value

        def __str__(self):
            return self.str_value
        
        @classmethod 
        def __enum_init__(cls):
            for i in range(len(cls.__values__)):
                setattr(cls, cls.__values__[i], CallPut(i+1, cls.__values__[i]))


    CallPut.__enum_init__()
            
t = CallPut.call
print( "Call: %s; Booleans: %r, %r " %(t, CallPut.call == t, CallPut.put == t) )
print( "Wrong type: %r" % (t == 1) )

2.7.10 (default, Dec 28 2015, 04:30:58) 
[GCC 5.2.1 20151010]
no enums
Call: call; Booleans: True, False 
Wrong type: False


In [4]:
def N(x):
    return stats.norm.cdf(x, 0.0, 1.0)

def NPrime(x):
    return stats.norm.pdf(x, 0.0, 1.0)

def bsm_d1(S, K, T, r, q, sigma):
    S = float(S)
    return (m.log(S / K) + (r - q + 0.5 * sigma ** 2) * T) / (sigma * m.sqrt(T))

def bsm_d2(S, K, T, r, q, sigma):
    S = float(S)
    return (m.log(S / K) + (r - q - 0.5 * sigma ** 2) * T) / (sigma * m.sqrt(T))

def bsm_pv(callPutType, S, K, T, r, q, sigma):
    d1 = bsm_d1(S, K, T, r, q, sigma)
    d2 = bsm_d2(S, K, T, r, q, sigma)
    if CallPut.call == callPutType:
        return S * N(d1) * m.exp(-q * T) - K * m.exp(-r * T) * N(d2)
    else:
        return K * N(-d2) * m.exp(-r * T)  - S * m.exp(-q * T) * N(-d1)

def bsm_delta(callPutType, S, K, T, r, q, sigma):
    d1 = bsm_d1(S, K, T, r, q, sigma)
    if CallPut.call == callPutType:
        return N(d1) * m.exp(-q * T)
    else:
        return -N(-d1) * m.exp(-q * T)



S0 = 80.; K = 85.; T = 1.0; r = 0.05; q = 0.0;
sigma = 0.2

S=100.; T=9./12.;sigma=0.2;r=0.05;q=0.0
ref_pv = bsm_pv(CallPut.call, S=S0, K=K, T=T, r=r, q=q, sigma=sigma)
y = lambda K: stats.norm.cdf((-(m.log(S / K) + (r - q + 0.5 * sigma ** 2) * T) / (sigma * m.sqrt(T))),0.0,1.0) * m.exp(-q * T)-0.5

KO = sp.optimize.brentq(y, 1e-10, 1000.)
print( "Brent's method: %.8f" % KO )

ref_delta = bsm_delta(CallPut.call, S=S0, K=K, T=T, r=r, q=q, sigma=sigma)
print( "ref_pv: %.6f, ref_delta: %.6f " % (ref_pv, ref_delta) )

Brent's method: 105.39025621
ref_pv: 4.699402, ref_delta: 0.481293 


$\frac{dS}{S} = r dt + \sigma dW_t$


$S(t) = S(t-\Delta t) \exp(r t - \frac{1}{2} \sigma^2 t + \sigma W_t )$

Разница между европейским и азиатским опционом в том, как рассчитывается $strike$. Если в европейском опционе он задается при заключении контракта, то в азиатском рассчитывается как некоторая функция от цены актива, на который и заключается договор, поэтому разница в функциях в том, что в mc_call_asian добавлен функционал рассчета страйка по симулируемым ценам.

In [ ]:
def mc_call_pv0(S0, K, T, r, sigma, M, I):
    # Simulating I paths with M time steps
    S = np.zeros((M + 1, I))
    S[0] = S0
    dt = float(T) / M
    for t in range(1, M + 1):
        z = np.random.standard_normal(I)
        S[t] = S[t - 1] * np.exp((r - 0.5 * sigma ** 2) * dt + sigma * m.sqrt(dt) * z)

    # Calculating the Monte Carlo estimator
    C = m.exp(-r * T) * np.sum(np.maximum(S[-1] - K, 0)) / I
    return C, S

def mc_call_pv_asian(S0, K, T, r, sigma, M, I):
    # Simulating I paths with M time steps
    prices = 0
    S = np.zeros((M + 1, I))
    S[0] = S0
    prices = S[0]
    dt = float(T) / M
    for t in range(1, M + 1):
        z = np.random.standard_normal(I)
        mean = np.mean(z)
        std = np.std(z)
        z = (z - mean)/std
        S[t] = S[t - 1] * np.exp((r - 0.5 * sigma ** 2) * dt + sigma * m.sqrt(dt) * z)
        prices += S[t]
    

    # Expected payoff
    #For Asian the strike price is the average of the all prices during the simulation
    K = prices / M
    E = np.sum(np.maximum(S[-1] - K, 0)) / I
    # PV
    C = m.exp(-r * T) * E
    return C, S

def mc_call_pv_european(S0, K, T, r, sigma, M, I):
    # Simulating I paths with M time steps
    S = np.zeros((M + 1, I))
    S[0] = S0
    dt = float(T) / M
    for t in range(1, M + 1):
        z = np.random.standard_normal(I)
        mean = np.mean(z)
        std = np.std(z)
        z = (z - mean)/std
        S[t] = S[t - 1] * np.exp((r - 0.5 * sigma ** 2) * dt + sigma * m.sqrt(dt) * z)
    

    # Expected payoff
    #For European
    E = np.sum(np.maximum(S[-1] - K, 0)) / I
    # PV
    C = m.exp(-r * T) * E
    return C, S

def mc_call_pv_european(S0, K, T, r, sigma, M, I):
    # Simulating I paths with M time steps
    S = np.zeros((M + 1, I))
    S[0] = K*np.exp(-r*T)
    dt = float(T) / M
    for t in range(1, M + 1):
        z = np.random.standard_normal(I)
        mean = np.mean(z)
        std = np.std(z)
        z = (z - mean)/std
        S[t] = S[t - 1] * np.exp((r - 0.5 * sigma ** 2) * dt + sigma * m.sqrt(dt) * z)
    

    # Expected payoff
    #For European
    E = np.sum(np.maximum(S[-1] - K, 0)) / I
    # PV
    C = m.exp(-r * T) * E
    return C, S

# Parameters
M = 360; I = 50000

np.random.seed(12345)
t0 = time()
C, SPaths = mc_call_pv0(S0, K, T, r, sigma, M, I)
calcTime = time() - t0


print( "PV: %.5f, abs diff: %.5f, rel diff:  %.5f" % (C, ref_pv - C, (ref_pv - C)/C) )
print( "Calculation time   %.5f" % calcTime )

np.random.seed(12345)
t0 = time()
C, SPaths = mc_call_pv_european(S0, K, T, r, sigma, M, I)
calcTime = time() - t0

print( "PV for european: %.5f, abs diff: %.5f, rel diff:  %.5f" % (C, ref_pv - C, (ref_pv - C)/C) )
print( "Calculation time   %.5f" % calcTime )

np.random.seed(12345)
t0 = time()
C, SPaths = mc_call_pv_asian(S0, K, T, r, sigma, M, I)
calcTime = time() - t0

print( "PV for asian: %.5f, abs diff: %.5f, rel diff:  %.5f" % (C, ref_pv - C, (ref_pv - C)/C) )
print( "Calculation time   %.5f" % calcTime )

PV: 4.67453, abs diff: 0.02487, rel diff:  0.00532
Calculation time   2.50454
PV for european: 5.64496, abs diff: -0.94555, rel diff:  -0.16750

In [8]:
dS = S0 / 1000.


np.random.seed(12345)
t0 = time()
C0, _ = mc_call_pv_european(S0, K, T, r, sigma, M, I)
C1, _ = mc_call_pv_european(S0+dS, K, T, r, sigma, M, I)
delta = (C1 - C0) / dS
calcTime = time() - t0

print( "Delta: %.5f, abs diff: %.5f, rel diff:  %.5f" % (delta, ref_delta - delta, (ref_delta - delta)/delta) )
print( "Calculation time   %.5f" % calcTime )

Delta: 0.52270, abs diff: -0.04140, rel diff:  -0.07921
Calculation time   9.85821


$\frac{ \partial C  }{ \partial S} \approx \frac{ C_{i+1} - C_{i-1} }{ 2 \Delta S }$

In [10]:
np.random.seed(12345)
t0 = time()
C_1, _ = mc_call_pv_european(S0-dS, K, T, r, sigma, M, I)
C1, _ = mc_call_pv_european(S0+dS, K, T, r, sigma, M, I)
delta = (C1 - C_1) / (2. * dS)
calcTime = time() - t0

print( "Delta: %.5f, abs diff: %.5f, rel diff:  %.5f" % (delta, ref_delta - delta, (ref_delta - delta)/delta) )
print( "Calculation time   %.5f" % calcTime )

Delta: 0.50215, abs diff: -0.02086, rel diff:  -0.04154
Calculation time   6.46342


-----